# KINACOの取得 と コンパイル

git clone https://lmr.aori.u-tokyo.ac.jp/feog/ymatsu/kinaco.git

cd kinaco  
git checkout summerschool2024  

cd src  
make  

 ## MPI並列を有効化するには
kinaco/ARCHを編集  
make clean  
make  

実行ファイル  nhm ができる  



In [ ]:
import sys
import math
import numpy as np
import matplotlib
import matplotlib.pyplot as plt

sys.path.append("PATH_TO_KINACO/python")

import kinaco

kinaco.calendar_format=1 #"YYYYMMDD_HHMMSS" 形式
kinaco.calendar_type  =2 #グレゴリオ暦



必要pythonパッケージ

numpy, f90nml, matplolib, moviepy, tqdm, IPython, Jupyter-notebook

不足するパッケージは
pip3 install f90nml --user 
とかでインストールしてください

# JCOPE-M (σ面 binary) を用いた粒子追跡

とりあえずは特定σ面での2次元追跡を想定
格子数 866, 620, 46  
C grid流速, ** U格子西面, V格子南面 **

Nx=864, Ny=616 に切り出し  
    U: i=2:, j=2:-2  
    V: i=1:-1, j=3:-1
    
LON: U.ctlからxdefを切り出し  
LAT: V.ctlからydefを切り出し

DX, DY: m単位での格子幅(2次元バイナリ)

MASK: 地形マスク,  四辺U,V=0 となる格子を定義  
(バイナリ、integer(1), 0:地形、1:海)  
通常は3次元だが、ここでは2次元  


In [ ]:
bindir = "BINARY/"

import xgrads
ctl = xgrads.CtlDescriptor(file=bindir+'U.ctl')
NX = len(ctl.xdef.samples) #元サイズ
lons = ctl.xdef.samples[1:]
nx = len(lons) - 1
np.savetxt('data/LON.txt', lons)

ctl = xgrads.CtlDescriptor(file=bindir+'V.ctl')
NY = len(ctl.ydef.samples) #元サイズ

lats = ctl.ydef.samples[2:-1]
ny = len(lats) - 1

np.savetxt('data/LAT.txt', lats)

nz = len(ctl.zdef.samples)

print(NX, NY, nx,ny,nz)

#m単位の格子幅をDX, DYに書き出す
#本データでは DXは東西一様、DYは全域一定だが、各格子毎に定義する

dx = np.ndarray((ny,nx))
dy = np.ndarray((ny,nx))

R = 6378E3 #地球半径
for j in range(ny):
    l = (lats[j]+lats[j+1])/2
    dy[j,:] = R*(lats[j+1]-lats[j])*math.pi/180

    for i in range(nx):
        dx[j,i] = R*math.cos(math.pi*l/180)*(lons[i+1]-lons[i])*math.pi/180

dx.astype('>f8').tofile('data/DX')
dy.astype('>f8').tofile('data/DY')


In [ ]:
date = '19930101'

U = np.fromfile(f"{bindir}/U_{date}", dtype='>f4', offset=24, count=NX*NY*nz).reshape((nz,NY,NX))
V = np.fromfile(f"{bindir}/V_{date}", dtype='>f4', offset=24, count=NX*NY*nz).reshape((nz,NY,NX))

k=0
U = U[k, 2:-2, 1:]
V = V[k, 2:-1, 1:-1]

ABSV = np.sqrt( (0.5*(U[:,1:]+U[:,:-1]))**2 + (0.5*(V[1:,:]+V[:-1,:]))**2)

mask = ABSV==0.0

(~mask).astype('i1').tofile('data/MASK')
#save the 2d mask for kinaco (integer(1) format)

ABSV = np.ma.masked_array(ABSV, mask)

ax = plt.gca()
c = ax.pcolorfast(lons, lats, ABSV)
plt.colorbar(c)

In [ ]:
#U, V 2Dデータの切り出し ここでは最上層 (k=0)とする
k=0
for t in kinaco.datetime_range('19930101', '19930109', '1D', include_start=True, include_end=True):
    t = str(t)

    U = np.fromfile(f"{bindir}/U_{t[:8]}", dtype='>f4', offset=24+k*(NX*NY)*4, count=NX*NY).reshape((NY,NX))
    U[2:-2,2:].tofile(f"data/U.{t}")
    
    V = np.fromfile(f"{bindir}/V_{t[:8]}", dtype='>f4', offset=24+k*(NX*NY)*4, count=NX*NY).reshape((NY,NX))
    V[3:-1,1:-1].tofile(f"data/V.{t}")

In [ ]:
#正しく切り出せているかの確認

t = '19930105_000000'
ax = plt.gca()
U = np.fromfile(f'data/U.{t}', dtype='>f4').reshape((ny,nx))
V = np.fromfile(f'data/V.{t}', dtype='>f4').reshape((ny,nx))
M = np.fromfile('data/MASK', dtype='i1').reshape((ny,nx))

absv = np.ma.masked_array(np.sqrt(U**2+V**2), M==0)
lon = np.loadtxt('data/LON.txt')
lat = np.loadtxt('data/LAT.txt')
c = ax.pcolorfast(lon, lat, absv)
plt.colorbar(c)

#なお、kinaco入力データのサイズは、U, Vもトレーサー等と同様に NX, NY, NZ格子数である
#したがって、南端・西端が開境界の場合はデータが欠損する。
# 南端のV, 西端のUを別途2次元断面ファイルとして与えることも可能であるが、省略すると自動的に補完する
# 

In [ ]:
#粒子初期位置決め
# csvファイルを作る
# 任意の数のカテゴリー定義可能

lon = np.loadtxt('data/LON.txt')
lat = np.loadtxt('data/LAT.txt')

with open('data/initial_particles.csv', 'w') as f:
#category 1: 22-23N, 125-126E
    cat = 1
    ID = 1
    #東西100x100 = 10000 個
    for x in np.linspace(125, 126, 100):
        for y in np.linspace(22, 23, 100): 
            #kinaco.x2i: 実座標を格子座標に変換
            #ここではLON.txt, LAT.txtから緯度経度を格子座標に投影
            i = kinaco.x2i(x, lon)
            j = kinaco.x2i(y, lat)
            f.write(f"{ID:8d}, {i:8.3f}, {j:8.3f}, 0.5, {cat:1d}\n")
            #2次元なので、zの初期位置は0.5 (1層目中央)
            ID += 1
            #IDは重複しなければ何でもよい. 0にしておけば内部で自動生成する
            
#category 2: 24-25N, 125-126E
    cat = 2
    ID = 100001
    for x in np.linspace(125, 126, 100):
        for y in np.linspace(24, 25, 100):
            i = kinaco.x2i(x, lon) 
            j = kinaco.x2i(y, lat)
            f.write(f"{ID:8d}, {i:8.3f}, {j:8.3f}, 0.5, {cat:1d}\n")
            ID += 1

#category 3: cat2 と同じ初期位置だが拡散を入れてみる(実行時指定)
    cat = 3
    ID = 200001
    for x in np.linspace(125, 126, 100):
        for y in np.linspace(24, 25, 100):
            i = kinaco.x2i(x, lon) 
            j = kinaco.x2i(y, lat)
            f.write(f"{ID:8d}, {i:8.3f}, {j:8.3f}, 0.5, {cat:1d}\n")
            ID += 1


#category 4: cat2 と同じ初期位置だが拡散を入れてみる(実行時指定)
    cat = 4
    ID = 300001
    for x in np.linspace(125, 126, 100):
        for y in np.linspace(24, 25, 100):
            i = kinaco.x2i(x, lon) 
            j = kinaco.x2i(y, lat)
            f.write(f"{ID:8d}, {i:8.3f}, {j:8.3f}, 0.5, {cat:1d}\n")
            ID += 1



In [ ]:
%cat RUNINFO.TEST

# データがそろったので実行する

コマンドラインにて

mkdir TEST  
mpirun -np 8 ./nhm < RUNINFO.TEST 

標準出力に順次経過出力がなされる
（RUNINFOでREPORTFILEを指定した場合はそのファイルに書き出されて画面には何も表示されない）


# Pythonで描画、解析

必要pythonパッケージ
numpy, f90nml, matplolib, moviepy, tqdm, IPython, Jupyter-notebook

In [ ]:
#描画

run = kinaco.read_config("RUNINFO.TEST")

lon = np.loadtxt("data/LON.txt")
lat = np.loadtxt("data/LAT.txt")
run.axis_x = lon
run.axis_y = lat

def draw_frame(W=None, E=None, S=None, N=None, *, ax=None):
    mask = np.fromfile('data/MASK', dtype='i1').reshape((ny,nx))

    if ax is None: ax = plt.gca()

    if W is None: W = lon[0]
    if E is None: E = lon[-1]
    if S is None: S = lat[0]
    if N is None: N = lat[-1]

    ax.pcolorfast(lon, lat, mask, cmap='gray')
    ax.set_xlim(W, E)
    ax.set_ylim(S, N)
    lonticks = kinaco.mkticks(W, E)
    latticks = kinaco.mkticks(S, N)
    ax.set_xticks(lonticks, kinaco.lonlabel(lonticks))
    ax.set_yticks(latticks, kinaco.latlabel(latticks))
    ax.set_aspect(1.2)


In [ ]:
def f(datetime):
    kinaco.calendar_type=2
    kinaco.calendar_format=1
    fig = plt.gcf()
    fig.clf()
    ax = fig.gca()
    ax.set_aspect(1.2)
    draw_frame(ax=ax)
    tab10 = plt.get_cmap('tab10')
    for i in range(1,2):
        #粒子データは run.read_particlesで読み込む
        #convert_pos は 格子座標を run.axis_x/y/z を元に実座標に変換 （ここではx:経度 y:緯度)
        p = run.read_particles(datetime=datetime, category=i+1, convert_pos=True)

        #pは構造体の配列, p['pos']が座標
        pos = p['pos']
        ax.scatter(pos[:,0], pos[:,1], color=tab10(i), s=0.25)
    ax.set_title(str(datetime))
    plt.tight_layout()

t = '19930102'
f(t)

In [ ]:
kinaco.mkanim(f, kinaco.datetime_range(run.start, run.end, "1D", include_start=False, include_end=True),
              "TEST.mp4", figsize=(12,9), dpi=120, fps=30, nthreads=8)

In [ ]:
from IPython.display import Video

Video('TEST.mp4', html_attributes="autoplay controls width='100%'")

In [ ]:
ids = 100, 100100, 200100, 300100, #とりあえずこの4粒子の軌跡を書いてみる

x = []
y = []
for t in kinaco.datetime_range(run.start, run.end, '1D', include_start=False, include_end=True):
    print('.', end='', flush=True)
    p = run.read_particles(datetime=t, idlist=ids, convert_pos=True)
    p = np.sort(p) #ID順にソート

    x.append(p['pos'][:,0])
    y.append(p['pos'][:,1])

x = np.asarray(x)
y = np.asarray(y)


In [ ]:
fig = plt.figure(figsize=(16,9), dpi=120)
ax = fig.gca()
draw_frame(ax=ax, E=140, N=35)

for i in range(4):
    ax.plot(x[:,i], y[:,i])